In [608]:
import numpy as np
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

sns.set()
import warnings
warnings.filterwarnings('ignore')



In [609]:
#Load the data and infer the date format for the date features

df = pd.read_csv('BikeSales-Dusty2.csv', 
                  parse_dates=['First_Seen','Last_Seen','Last_Modified'], 
                  infer_datetime_format=True)



In [610]:
df.head()

ABS Adjustable_Seat                                Bike               Body  \
0  No              No                        Kuda Pro 250  Adventure Touring   
1  No              No         250 R Road Manual 5sp 250cc        Super Sport   
2  No              No                               GN250              Naked   
3  No              No  GSX1100 ESD Road Manual 5sp 1100cc      Sport Touring   
4  No              No        TS250 Trail Manual 5sp 250cc              Trail   

     Bore                     Cam_Type        Carburettor  Carburettor(s)  \
0  62.000  SOHC (Single Over Head Cam)                NaN             1.0   
1  77.000  SOHC (Single Over Head Cam)                NaN             1.0   
2  72.000  SOHC (Single Over Head Cam)                NaN             1.0   
3  74.352  DOHC (Double Over Head Cam)  Constant velocity             4.0   
4  81.441                   Reed Valve                NaN             1.0   

                    Charging_Method  Clutch_Type   ...    Valves_Per_Cylinder  \
0  Alternator & Regulator-Rectifier  Multi plate   ...                    4.0   
1                            Engine  Multi plate   ...                    4.0   
2                            Engine          NaN   ...                    4.0   
3                            Engine          NaN   ...                    4.0   
4                            Engine          NaN   ...                    4.0   

   Warranty_KMs Warranty_in_Months_from_First_Registration  \
0            No                                          3   
1            No                                          0   
2            No                                          0   
3            No                                          0   
4            No                                          0   

  Wet_Operational_Weight  Wheel_Type Wheelbase    Width  Windscreen  \
0                  150.0       Other    1480.0  860.000    Standard   
1                  136.0     9-Spoke    1350.0  818.770    Standard   
2                  141.0         NaN    1499.0  815.305    Standard   
3                  253.0         NaN    1440.0  769.585    Standard   
4                  141.0         NaN    1399.0  818.770    Standard   

  Release_Year   Seller  
0         2009  Private  
1         2013  Private  
2         1991  Private  
3         1984  Private  
4         1976  Private  

[5 rows x 91 columns]

In [611]:
#######################################################################
### DELETE CELL WHEN MACHINE LEARNING IMPUTATION HAS BEEN COMPLETED ###
#######################################################################

# The EDA notebook will eventually perform machine learning on these features to impute the missing values.
# Just so there isn't any issues with the data for feature engineering, i'l be using the most common value.

df['Body'][df['Body'].isnull() == True] = df['Body'].mode()[0]
df['Carburettor'][df['Carburettor'].isnull() == True] = df['Carburettor'].mode()[0]
df['Clutch_Type'][df['Clutch_Type'].isnull() == True] = df['Clutch_Type'].mode()[0]
df['Country_of_Origin'][df['Country_of_Origin'].isnull() == True] = df['Country_of_Origin'].mode()[0]
df['Drive_Type'][df['Drive_Type'].isnull() == True] = df['Drive_Type'].mode()[0]
df['Frame_Material'][df['Frame_Material'].isnull() == True] = df['Frame_Material'].mode()[0]
df['Front_Brake_Description'][df['Front_Brake_Description'].isnull() == True] = df['Front_Brake_Description'].mode()[0]
df['Front_Suspension'][df['Front_Suspension'].isnull() == True] = df['Front_Suspension'].mode()[0]
df['Rear_Brake_Description'][df['Rear_Brake_Description'].isnull() == True] = df['Rear_Brake_Description'].mode()[0]
df['Rear_Suspension'][df['Rear_Suspension'].isnull() == True] = df['Rear_Suspension'].mode()[0]
df['Wheel_Type'][df['Wheel_Type'].isnull() == True] = df['Wheel_Type'].mode()[0]

df['Kilometers'][df['Kilometers'].isnull() == True] = df['Kilometers'].mean()


df['Body'][df['Body'].str.contains('MY') == True] = \
    df['Body'][df['Body'].str.contains('MY') == True].str.split().str[:-1].str.join(' ');


## Brand
This is the manufacturer of the vehicle and is the same as the Make of the bike. This is a common way to distinguish between bike at the simplest level. 


In [612]:
# Features to extract from the data
# Brand, model, Age, 
df['Brand'] = df['URL'].str.split('/').str[5].str.split('-').str[1].str.capitalize()

# Replace known names with more than one word, like Harley Davidson
df['Brand'][df['Brand'] == 'Harley'] = 'Harley Davidson'
df['Brand'][df['Brand'] == 'Mv'] = 'MV Agusta'
df['Brand'][df['Brand'] == 'Royal'] = 'Royal Enfield'
df['Brand'][df['Brand'] == 'Moto'] = 'Moto Guzzi'
df['Brand'][df['Brand'] == 'Can'] = 'Can Am'




## Model
This describes the Brand of the bike in more detail, providing a slightly more complex discription. 

In [613]:
df['Model'] = df['URL'].str.split('/').str[5].str.split('-').str[2:].str.join(' ').str.capitalize()

# Need to deal with the models that have two word, like Harley Davidson
df['Model'][df['Model'].str.contains('Davidson') == True] = \
    df['Model'][df['Model'].str.contains('Davidson') == True].str.split().str[1:].str.join(' ');
df['Model'][df['Model'].str.contains('Agusta') == True] = \
    df['Model'][df['Model'].str.contains('Agusta') == True].str.split().str[1:].str.join(' ');
df['Model'][df['Model'].str.contains('Enfield') == True] = \
    df['Model'][df['Model'].str.contains('Enfield') == True].str.split().str[1:].str.join(' ');
df['Model'][df['Model'].str.contains('Guzzi') == True] = \
    df['Model'][df['Model'].str.contains('Guzzi') == True].str.split().str[1:].str.join(' ');
df['Model'][df['Model'].str.contains('Am') == True] = \
    df['Model'][df['Model'].str.contains('Am') == True].str.split().str[1:].str.join(' ');



In [614]:
# Remove the MY YY from the end of the Model description.
# This is the effective year, the bike was registerd on the road
df['Model'][df['Model'].str.contains('my') == True] = \
    df['Model'][df['Model'].str.contains('my') == True].str.split().str[:-1].str.join(' ');
df['Model'][df['Model'].str.contains('MY') == True] = \
    df['Model'][df['Model'].str.contains('MY') == True].str.split().str[:-1].str.join(' ');


## Age
Any asset decreasing in value with age. We can deterime the age using todays date and the release year.

In [615]:
df['Age'] = datetime.now().year - df['Release_Year']

## Time to Sale
This will be the time it takes to sell the bike. We can assume the bike is sold if the last time the advertisement was seen, isn't the most recent time. ie, the advertisement has been taken down. We will assume this means the bike has been sold, even though the seller could have decided to not sell the bike.

In [616]:
days = (df['Last_Seen'] - df['First_Seen'])
df['Time_to_Sale'] = days.astype('timedelta64[D]')

# Correct for bike that have not been sold yet
df['Time_to_Sale'][(df['Last_Seen'] == df['Last_Seen'].max()) == True] = 0


In [617]:

df.to_csv('Bikesales_Features.csv',index=False)

In [618]:
df_numbers = df.select_dtypes(include='number')

In [619]:
sns.pairplot(df_numbers)

In [ ]:
sns.pairplot(sport[list(sport.select_dtypes(include='number').columns)])

In [ ]:
df.head()

In [ ]:
df.shape

In [ ]:
sport = df[df['Body'].str.contains('Sport') == True]
sport_numbers = sport.select_dtypes(include='number')
sport_numbers.shape


In [ ]:
numerical_features = list(df.select_dtypes(include='number').columns)
#categorical_features = list(df.select_dtypes(exclude='number').columns)

# categorical_features = ['Bike', 'Body', 'Colour', 'Cooling', 'Country_of_Origin', 
#                         'Engine_Config', 'Fuel_Type', 'State', 'Suburb', 'Seller', 
#                         'Brand', 'Model'] # (21396, 11974)

categorical_features = ['Bike', 'Body', 'Brand', 'Model', 'Seller'] # (21396, 8785)

In [ ]:
def add_dummy_variables(df, categorical_features):
    
    additional = pd.get_dummies(df[categorical_features])
    df[additional.columns] = additional
    return df.drop(categorical_features, axis=1)
    


In [ ]:
sport = add_dummy_variables(sport, categorical_features)

In [ ]:
# numerical_features = list(sport.select_dtypes(include='number').columns)
# sport = sport[numerical_features]
# sport.drop(['Time_to_Sale'], axis=1, inplace=True)
# sport.shape # (5343, 1463)



In [ ]:
sport.head()

In [ ]:
sport.describe()

In [ ]:
#sns.pairplot(sport[features])

In [ ]:
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import accuracy_score, confusion_matrix, mean_squared_error
from sklearn.metrics import classification_report


In [ ]:
sport = sport.select_dtypes(include='number')


In [ ]:

target = 'Price'
features = list(set(sport.columns) - set([target]))

sc = StandardScaler()
sc.fit(sport)
s = sc.transform(sport)
scaleSport = pd.DataFrame(s,columns=sport.columns)

X = scaleSport[features]
y = scaleSport[target]


X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1)


In [ ]:

model = RandomForestRegressor(n_estimators=100, max_depth=2, random_state=0)
model.fit(X_train, y_train)

pred = model.predict(X_test)



In [ ]:
model.score(X_test,y_test)

In [ ]:
model.score(X_train,y_train)

In [ ]:
model.score(X, y)

In [ ]:
#model.r2_score(y_test,pred)

In [ ]:
#model.classification_report(y_test,pred)

In [ ]:
#print ('accuracy:',accuracy_score(y_test,pred))
print ('mean_squared_error:',mean_squared_error(y_test,pred))

In [ ]:
plt.scatter(y_test,pred)

In [ ]:
def feature_plot(model,X,top=10):
    
    feats_imp = pd.DataFrame(model.feature_importances_, index=X.columns, columns=['FeatureImportance'])
    feats_imp = feats_imp.sort_values('FeatureImportance', ascending=False)[:top]

    feats_imp.plot(kind='barh', figsize=(12,6), legend=False)
    plt.title('Feature Importance from XgBoost Classifier')
    sns.despine(left=True, bottom=True)
    plt.gca().invert_yaxis()
    
feature_plot(model,X)

In [ ]:
len(model.feature_importances_)

In [ ]:
feats_imp = pd.DataFrame(model.feature_importances_, index=X.columns, columns=['FeatureImportance'])
feats_imp = feats_imp.sort_values('FeatureImportance', ascending=False)[:10]

feats_imp

In [ ]:
# Forward Feature selection


sport_numbers.head()